<a href="https://colab.research.google.com/github/shozy-frenia/Geomat/blob/main/Extendedsolution.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!sudo apt update
!sudo apt install libcairo2-dev ffmpeg texlive texlive-latex-extra texlive-fonts-extra texlive-latex-recommended texlive-science libpango1.0-dev
!pip install manim

Hit:1 https://cli.github.com/packages stable InRelease
Hit:2 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease
Hit:3 https://r2u.stat.illinois.edu/ubuntu jammy InRelease
Hit:4 http://security.ubuntu.com/ubuntu jammy-security InRelease
Hit:5 http://archive.ubuntu.com/ubuntu jammy InRelease
Hit:6 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:7 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Hit:8 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:9 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu jammy InRelease
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
103 packages can be upgraded. Run 'apt list --upgradable' to see them.
W: Skipping acquire of configured file 'main/source/Sources' as repository 'https://r2u.stat.illinois.edu/ubuntu jammy InRelease' does not seem to provide it (sources.list entry misspelt?)
Reading package lists... Done
Building dependency tre

In [3]:
from manim import *
import numpy as np

class Solution(Scene):
    def construct(self):
        r1, r2 = 1.6, 1.1
        c1 = LEFT * 2.5
        c2 = RIGHT * 2.5

        w1 = Circle(radius=r1, color=BLUE).move_to(c1)
        w2 = Circle(radius=r2, color=GREEN).move_to(c2)

        dist = np.linalg.norm(c1 - c2)
        av = np.arccos((r1 - r2) / dist)

        A = c1 + r1 * np.array([np.cos(av),  np.sin(av),  0])
        B = c2 + r2 * np.array([np.cos(av),  np.sin(av),  0])
        C = c1 + r1 * np.array([np.cos(-av), np.sin(-av), 0])
        D = c2 + r2 * np.array([np.cos(-av), np.sin(-av), 0])

        line_ab = Line(A, B, color=WHITE)
        line_cd = Line(C, D, color=WHITE)

        v_cb = (B - C) / np.linalg.norm(B - C)
        P = C + 2 * np.dot(c1 - C, v_cb) * v_cb
        v_ad = (A - D) / np.linalg.norm(A - D)
        Q = D + 2 * np.dot(c2 - D, v_ad) * v_ad

        ang_p = np.arctan2(P[1] - c1[1], P[0] - c1[0])
        ang_q = np.arctan2(Q[1] - c2[1], Q[0] - c2[0])

        tan_p_full = TangentLine(w1, alpha=(ang_p % (2*PI))/(2*PI), length=20, color=YELLOW)
        tan_q_full = TangentLine(w2, alpha=(ang_q % (2*PI))/(2*PI), length=20, color=GOLD)

        M       = line_intersection((A, B), tan_p_full.get_start_and_end())
        M_prime = line_intersection((A, B), tan_q_full.get_start_and_end())
        F       = line_intersection((C, D), tan_p_full.get_start_and_end())
        L       = line_intersection((C, D), tan_q_full.get_start_and_end())

        # Обрезанные касательные F→M и L→M'
        tan_p_cut = Line(F, M, color=YELLOW)
        tan_q_cut = Line(L, M_prime, color=GOLD)

        def lbl(text, point, direction=UP, color=WHITE, size=22):
            return Text(text, font_size=size, color=color).next_to(point, direction, buff=0.15)

        def angle_arc(vertex, p1, p2, radius=0.3, color=WHITE):
            v1 = (p1 - vertex) / np.linalg.norm(p1 - vertex)
            v2 = (p2 - vertex) / np.linalg.norm(p2 - vertex)
            a1 = np.arctan2(v1[1], v1[0])
            a2 = np.arctan2(v2[1], v2[0])
            diff = (a2 - a1) % (2 * PI)
            if diff > PI:
                a1, a2 = a2, a1
                diff = (2 * PI) - diff
            return Arc(radius=radius, start_angle=a1, angle=diff,
                               arc_center=vertex, color=color, stroke_width=2)

        def angle_label(text, vertex, p1, p2, radius=0.3, color=WHITE, font_size=16):
            v1 = (p1 - vertex) / np.linalg.norm(p1 - vertex)
            v2 = (p2 - vertex) / np.linalg.norm(p2 - vertex)
            bis = v1 + v2
            if np.linalg.norm(bis) < 1e-6:
                bis = np.array([-v1[1], v1[0], 0])
            else:
                bis = bis / np.linalg.norm(bis)
            return Text(text, font_size=font_size, color=color).move_to(
                       vertex + bis * (radius + 0.22))

        # Засечка на середине отрезка (перпендикулярная чёрточка)
        def tick(p1, p2, color=WHITE, size=0.10):
            mid = (p1 + p2) / 2
            d = p2 - p1
            perp = np.array([-d[1], d[0], 0])
            perp = perp / np.linalg.norm(perp) * size
            return Line(mid - perp, mid + perp, color=color, stroke_width=3)

        # ── Заголовок ──────────────────────────────────────────────────────
        title = Text("Zadacha No5", font_size=28, color=YELLOW).to_edge(UP)
        self.play(Write(title))
        self.wait(0.3)

        # ── Шаг 1: окружности и касательные ───────────────────────────────
        step1 = Text("w1, w2 — okruzhnosti;  AB i CD — obshchie vneshnie kasatelnye",
                           font_size=17, color=GRAY_A).to_edge(DOWN)
        self.play(Create(w1), Create(w2), Write(step1))
        self.play(Create(line_ab), Create(line_cd))
        dots_abcd = VGroup(Dot(A,color=WHITE),Dot(B,color=WHITE),Dot(C,color=WHITE),Dot(D,color=WHITE))
        lbls_abcd = VGroup(lbl("A",A,UL),lbl("B",B,UR),lbl("C",C,DL),lbl("D",D,DR))
        self.play(FadeIn(dots_abcd), Write(lbls_abcd))
        self.wait(1)

        # ── Шаг 2: равнобокая трапеция ────────────────────────────────────
        self.play(FadeOut(step1))
        step2 = Text("Shag 1: ABDC — ravnobokaya trapeciya", font_size=18, color=TEAL).to_edge(DOWN)
        self.play(Write(step2))
        side_ac = Line(A, C, color=ORANGE)
        side_bd = Line(B, D, color=ORANGE)
        self.play(Create(side_ac), Create(side_bd))
        self.wait(0.5)
        self.play(FadeOut(step2))

        r1txt = Text("AC || BD  =>  parallely", font_size=17, color=ORANGE).to_edge(DOWN)
        self.play(Write(r1txt))
        self.play(side_ac.animate.set_color(YELLOW), side_bd.animate.set_color(YELLOW))
        self.wait(0.8)
        self.play(side_ac.animate.set_color(ORANGE), side_bd.animate.set_color(ORANGE))
        self.play(FadeOut(r1txt))

        r2txt = Text("AB = CD  =>  ABDC ravnobokaya trapeciya", font_size=16, color=GREEN).to_edge(DOWN)
        self.play(Write(r2txt))
        self.play(line_ab.animate.set_color(GREEN), line_cd.animate.set_color(GREEN))
        self.wait(1.2)
        trap_box = Text("ABDC — ravnobokaya trapeciya  (AC||BD,  AB=CD)", font_size=19, color=WHITE)
        trap_rect = SurroundingRectangle(trap_box, color=YELLOW, buff=0.15)
        VGroup(trap_box, trap_rect).next_to(title, DOWN, buff=0.12)
        self.play(FadeOut(r2txt), Write(trap_box), Create(trap_rect))
        self.wait(0.8)
        self.play(line_ab.animate.set_color(WHITE), line_cd.animate.set_color(WHITE))

        # ── Шаг 3: секущие P и Q ──────────────────────────────────────────
        step3 = Text("Shag 2: CB sech. w1 v P;  AD sech. w2 v Q",
                                     font_size=17, color=GRAY_A).to_edge(DOWN)
        self.play(Write(step3))
        sec_cb = Line(C, B, color=BLUE_A, stroke_opacity=0.5)
        sec_ad = Line(A, D, color=GREEN_A, stroke_opacity=0.5)
        self.play(Create(sec_cb), Create(sec_ad))
        dot_p = Dot(P, color=YELLOW)
        dot_q = Dot(Q, color=GOLD)
        self.play(FadeIn(dot_p), FadeIn(dot_q),
                       Write(lbl("P",P,LEFT,YELLOW)), Write(lbl("Q",Q,RIGHT,GOLD)))
        self.wait(1)

        # ── Шаг 4: касательные F→M и L→M' ────────────────────────────────
        self.play(FadeOut(step3))
        step4 = Text(
                "Shag 3: kasatelnaya v P -> AB v M, CD v F\n"
                        "kasatelnaya v Q -> AB v M', CD v L",
                          font_size=16, color=GRAY_A, line_spacing=1.2).to_edge(DOWN)
        self.play(Write(step4))

        self.play(Create(tan_p_cut))
        dot_M = Dot(M, color=YELLOW, radius=0.09)
        dot_F = Dot(F, color=YELLOW, radius=0.09)
        lbl_M = lbl("M", M, UP+LEFT*0.15, YELLOW, size=22)
        lbl_F = lbl("F", F, DOWN+LEFT*0.15, YELLOW, size=22)
        self.play(FadeIn(dot_M), FadeIn(dot_F), Write(lbl_M), Write(lbl_F))
        self.wait(0.4)

        self.play(Create(tan_q_cut))
        dot_Mprime = Dot(M_prime, color=GOLD, radius=0.09)
        dot_L = Dot(L, color=GOLD, radius=0.09)
        lbl_Mprime = lbl("M'", M_prime, UP+RIGHT*0.15, GOLD, size=22)
        lbl_L = lbl("L", L, DOWN+RIGHT*0.15, GOLD, size=22)
        self.play(FadeIn(dot_Mprime), FadeIn(dot_L), Write(lbl_Mprime), Write(lbl_L))
        self.wait(1)

        # ── Шаг 5: α = ∠BAD = ∠BCD (смотрят на дугу BD) ──────────────────
        # ИСПРАВЛЕНО: α = ∠BAD: при вершине A, лучи к B и к D (не к C!)
        # α = ∠BCD: при вершине C, лучи к B и к D
        self.play(FadeOut(step4))
        step5 = Text(
                "Shag 4: <BAD = <BCD  (oba smotryat na dogu BD)  =>  alpha = beta",
                      font_size=16, color=TEAL).to_edge(DOWN)
        self.play(Write(step5))

        # α на A: угол BAD (лучи к B и к D) — ИСПРАВЛЕНО
        arc_BAD  = angle_arc(A, B, D, radius=0.35, color=TEAL)
        mark_BAD = angle_label("α", A, B, D, radius=0.35, color=TEAL, font_size=18)
        # α на C: угол BCD (лучи к B и к D)
        arc_BCD  = angle_arc(C, B, D, radius=0.35, color=TEAL)
        mark_BCD_a = angle_label("α", C, B, D, radius=0.35, color=TEAL, font_size=18)
        self.play(Create(arc_BAD), Write(mark_BAD), Create(arc_BCD), Write(mark_BCD_a))
        self.wait(1.5)
        # Убираем α на C — там будет β
        self.play(FadeOut(mark_BCD_a), FadeOut(arc_BCD), FadeOut(step5))

        # ── Шаг 6: β — △CFP равнобедренный ──────────────────────────────
        # ИСПРАВЛЕНО: CF = FP (касательные из C: CF и CP... нет — CF и FP)
        # Точнее: из точки C касательные к w1: отрезок CA (касательная) и CP (секущая касательная)
        # Равные касательные из C: CF = CP => треугольник CFP равнобедренный
        # Засечки: CF = FP (т.е. тики на CF и FP)
        step6 = Text(
                "Shag 5: CF=FP (kasatelnye iz C k w1) => trg CFP ravnobedr.\n"
                        "=> <BCD = <PCF = <CPF = <MPB",
                                font_size=15, color=ORANGE, line_spacing=1.2).to_edge(DOWN)
        self.play(Write(step6))

        tri_CFP = Polygon(C, F, P, color=ORANGE, fill_opacity=0.10, stroke_width=2)
        self.play(Create(tri_CFP))

        # ИСПРАВЛЕНО: Засечки CF = FP (равные касательные из C к w1)
        tk_CF = tick(C, F, color=ORANGE, size=0.10)
        tk_FP = tick(F, P, color=ORANGE, size=0.10)
        self.play(Create(tk_CF), Create(tk_FP))

        # β на C: угол PCF
        arc_PCF = angle_arc(C, P, F, radius=0.28, color=ORANGE)
        t_PCF   = angle_label("β", C, P, F, radius=0.28, color=ORANGE, font_size=16)
        # β на P: угол CPF (вершина P, лучи к C и F)
        arc_CPF = angle_arc(P, C, F, radius=0.28, color=ORANGE)
        t_CPF   = angle_label("β", P, C, F, radius=0.28, color=ORANGE, font_size=16)
        # β на P: угол MPB (вершина P, лучи к M и B)
        arc_MPB = angle_arc(P, M, B, radius=0.36, color=ORANGE)
        t_MPB   = angle_label("β", P, M, B, radius=0.36, color=ORANGE, font_size=16)

        self.play(
                Create(arc_PCF), Write(t_PCF),
                        Create(arc_CPF), Write(t_CPF),
                                Create(arc_MPB), Write(t_MPB),
                )
        self.wait(1.5)
        self.play(FadeOut(step6))

        # ── Шаг 7: γ — △DQL равнобедренный ──────────────────────────────
        # ИСПРАВЛЕНО: QL = LD (не QD=DL, а QL=LD — тики на QL и LD)
        step7 = Text(
                "Shag 6: QL=LD (kasatelnye iz D k w2) => trg DQL ravnobedr.\n"
                        "=> <ABC = <ADC = <QDL = <DQL = <M'QA",
                                font_size=15, color=GREEN_B, line_spacing=1.2).to_edge(DOWN)
        self.play(Write(step7))

        tri_DQL = Polygon(D, Q, L, color=GREEN_B, fill_opacity=0.10, stroke_width=2)
        self.play(Create(tri_DQL))

        # ИСПРАВЛЕНО: Засечки QL = LD (равные касательные из D к w2)
        tk_QL = tick(Q, L, color=GREEN_B, size=0.10)
        tk_LD = tick(L, D, color=GREEN_B, size=0.10)
        self.play(Create(tk_QL), Create(tk_LD))

        # γ = ∠ABC при B (лучи к A и C)
        arc_ABC = angle_arc(B, A, C, radius=0.32, color=GREEN_B)
        t_ABC   = angle_label("γ", B, A, C, radius=0.32, color=GREEN_B, font_size=16)
        # γ = ∠ADC при D (только дуга, метка слипнется с QDL)
        arc_ADC = angle_arc(D, A, C, radius=0.34, color=GREEN_B)
        # γ = ∠QDL при D (меньший радиус)
        arc_QDL = angle_arc(D, Q, L, radius=0.21, color=GREEN_B)
        t_QDL   = angle_label("γ", D, Q, L, radius=0.21, color=GREEN_B, font_size=16)
        # γ = ∠DQL при Q (лучи к D и L)
        arc_DQL = angle_arc(Q, D, L, radius=0.28, color=GREEN_B)
        t_DQL   = angle_label("γ", Q, D, L, radius=0.28, color=GREEN_B, font_size=16)
        # γ = ∠M'QA при Q (лучи к M' и A)
        arc_MQA = angle_arc(Q, M_prime, A, radius=0.42, color=GREEN_B)
        t_MQA   = angle_label("γ", Q, M_prime, A, radius=0.42, color=GREEN_B, font_size=16)

        self.play(
                Create(arc_ABC), Write(t_ABC),
                        Create(arc_ADC),
                                Create(arc_QDL), Write(t_QDL),
                                        Create(arc_DQL), Write(t_DQL),
                                                Create(arc_MQA), Write(t_MQA),
                )
        self.wait(1.5)
        self.play(FadeOut(step7))

        # ── Шаг 8: δ = ∠BMP и ∠AM'Q ─────────────────────────────────────
        step8 = Text(
                "Iz cepochek: <MPB = <M'QA  i  <MBP = <M'AD\n"
                        "=> <AM'Q = <BMP",
                              font_size=16, color=PINK, line_spacing=1.2).to_edge(DOWN)
        self.play(Write(step8))

        arc_BMP = angle_arc(M,       B, P, radius=0.28, color=PINK)
        t_BMP   = angle_label("δ", M,       B, P, radius=0.28, color=PINK, font_size=16)
        arc_AMQ = angle_arc(M_prime, A, Q, radius=0.28, color=PINK)
        t_AMQ   = angle_label("δ", M_prime, A, Q, radius=0.28, color=PINK, font_size=16)
        self.play(Create(arc_BMP), Write(t_BMP), Create(arc_AMQ), Write(t_AMQ))
        self.wait(1.5)
        self.play(FadeOut(step8))

        # ── Шаг 9: степень точки + теорема синусов ────────────────────────
        tri_BMP2 = Polygon(B, M,       P, color=YELLOW, fill_opacity=0.08, stroke_width=2)
        tri_MQA2 = Polygon(M_prime, Q, A, color=GOLD,   fill_opacity=0.08, stroke_width=2)
        self.play(Create(tri_BMP2), Create(tri_MQA2))
        self.wait(0.5)

        # Формула степени точки — сверху слева, не перекрывает схему
        formula_top = MathTex(
                r"AB^2 = BP \cdot BC = AQ \cdot AD \;\Rightarrow\; AQ = BP",
                            font_size=30, color=TEAL
                        ).to_corner(UL).shift(DOWN * 1.2 + RIGHT * 0.3)
        self.play(Write(formula_top))
        self.wait(0.8)

        # Теорема синусов — снизу слева, свободное место
        formula_sin = MathTex(
                r"\frac{AQ}{\sin \angle AM'Q} = \frac{BP}{\sin \angle BMP}"
                        r"= \frac{BM}{\sin \angle BPM} = \frac{M'Q}{\sin \angle M'AQ}",
                                  font_size=28, color=GREEN
                                      ).to_corner(DL).shift(UP * 0.1 + RIGHT * 0.1)
        self.play(Write(formula_sin))
        self.wait(2.5)
        self.play(FadeOut(formula_top), FadeOut(formula_sin))

        # Вывод
        step9c = Text(
                "<BPM = <M'AQ  =>  BM = M'Q\n"
                        "M'Q = BM'  =>  BM = BM'  =>  M = M'",
                                font_size=16, color=RED, line_spacing=1.2).to_edge(DOWN)
        self.play(Write(step9c))

        self.play(
                FadeOut(tri_BMP2), FadeOut(tri_MQA2),
                        Indicate(dot_M,      scale_factor=1.8, color=RED),
                                Indicate(dot_Mprime, scale_factor=1.8, color=RED),
                        )
        self.wait(0.5)
        self.play(
                dot_Mprime.animate.move_to(M).set_color(RED),
                        lbl_Mprime.animate.next_to(M, UP * 2.2).set_color(RED),
                        run_time=1.5
                            )
        self.wait(0.5)

        # ── Финал ─────────────────────────────────────────────────────────
        self.play(FadeOut(step9c))
        final_text = Text("M = M'  =>  kasatelnye peresek. na AB  ✓", font_size=20, color=RED)
        final_box  = SurroundingRectangle(final_text, color=RED, buff=0.2)
        VGroup(final_text, final_box).to_edge(DOWN)
        self.play(Write(final_text), Create(final_box))
        self.play(line_ab.animate.set_color(RED))
        self.play(Indicate(dot_M, scale_factor=2, color=RED))
        self.wait(2)

In [4]:
%manim -v WARNING -qh Solution

Manim Community v0.20.0